In [1]:
import torch
from torch import nn

torch.cuda.empty_cache()

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
%cd drive/MyDrive/moj7

/content/drive/MyDrive/moj7


In [4]:
!ls

config.txt	 in-header.tsv	out-header.tsv	     test-A
dev-0		 model1.bin	processed_train.txt  train
filename.pickle  model2.bin	simplepredict.py     train_new.txt


In [5]:
import pandas as pd
import regex as re
import csv

def clean_text(text):
    text = text.lower().replace('-\\\\\\\\n', '').replace('\\\\\\\\n', ' ')
    text = re.sub(r'\p{P}', '', text)
    text = text.replace("'t", " not").replace("'s", " is").replace("'ll", " will").replace("'m", " am").replace("'ve", " have")

    return text

In [6]:
train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
train_labels = pd.read_csv('train/expected.tsv', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)

train_data = train_data[[6, 7]]
train_data = pd.concat([train_data, train_labels], axis=1)

train_data['text'] = train_data[6] + train_data[0] + train_data[7]
train_data = train_data[['text']]

with open('processed_train.txt', 'w', encoding='utf-8') as file:
    for _, row in train_data.iterrows():
        text = clean_text(str(row['text']))
        file.write(text + '\n')

<ipython-input-6-c2ca5c6b11cc>:1: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
<ipython-input-6-c2ca5c6b11cc>:1: FutureWarning: The warn_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
<ipython-input-6-c2ca5c6b11cc>:2: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_labels = pd.read_csv('train/expected.tsv', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
<ipython-input-6-c2ca5c6b11cc>:2: FutureWarning: The warn_bad_l

In [7]:
import itertools
import lzma
import numpy as np
import regex as re
import torch
import pandas as pd
from torch import nn
from torch.utils.data import IterableDataset, DataLoader
import csv
from itertools import islice, chain
from torchtext.vocab import build_vocab_from_iterator

In [8]:
device='cuda'

In [9]:
train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
train_labels = pd.read_csv('train/expected.tsv', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
train_data = train_data[[6, 7]]
train_data = pd.concat([train_data, train_labels], axis=1)
train_data['text'] = train_data[6] + train_data[0] + train_data[7]
train_data = train_data[['text']]

<ipython-input-9-28a7685109f8>:1: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
<ipython-input-9-28a7685109f8>:1: FutureWarning: The warn_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_data = pd.read_csv('train/in.tsv.xz', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
<ipython-input-9-28a7685109f8>:2: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_labels = pd.read_csv('train/expected.tsv', sep='\t', error_bad_lines=False, warn_bad_lines=False, header=None, quoting=csv.QUOTE_NONE)
<ipython-input-9-28a7685109f8>:2: FutureWarning: The warn_bad_l

In [10]:
train_data

text
0       came fiom the last place to this\nplace, and t...
1       MB. BOOT'S POLITICAL OBEED\nAttempt to imagine...
2       "Thera were in 1771 only aeventy-nine\n*ub*erl...
3       A gixnl man y nitereRtiiiv dii-clos-\nur«s reg...
4       Tin: 188UB TV THF BBABBT QABJE\nMr. Schiffs *t...
...                                                   ...
432017  Sam Clendenin bad a fancy for Ui«\nscience of ...
432018  Wita.htt halting the party ware dilven to the ...
432019  It was the last thing that either of\nthem exp...
432020  settlement with the department.\nIt is also sh...
432021  Flour quotations—low extras at 1 R0®2 50;\ncit...

[432022 rows x 1 columns]

In [11]:
with open('train_new.txt', 'w', encoding='utf-8') as file:
    for _, row in train_data.iterrows():
        text = clean_text(str(row['text']))
        file.write(text + '\n')



In [12]:
class SimpleTrigramNeuralLanguageModel(nn.Module):
    def __init__(self, vocabulary_size, embedding_size, hidden_size):
        super(SimpleTrigramNeuralLanguageModel, self).__init__()
        self.embedding = nn.Embedding(vocabulary_size * 2, embedding_size)
        self.linear1 = nn.Linear(embedding_size, hidden_size)
        self.linear2 = nn.Linear(hidden_size, vocabulary_size * 2)

    def forward(self, x):
        x = self.embedding(x)
        x = self.linear1(x)
        x = self.linear2(x)
        x = torch.softmax(x, dim=1)
        return x

In [13]:
vocab_size = 38000
embed_size = 300
hidden_size = 256

In [14]:
def words_line(line):
    line = line.rstrip()
    yield '<s>'
    for m in re.finditer(r'[\p{L}0-9\*]+|\p{P}+', line):
        yield m.group(0).lower()
    yield '</s>'

def file_words(file_name):
    with open(file_name, 'r', encoding='utf-8') as fh:
        for line in fh:
            yield words_line(line)

In [15]:
def iterator_look(gen):
    first_prev = None
    sec_prev = None
    for item in gen:
        if first_prev and sec_prev:
            yield (sec_prev+ first_prev, item)
        sec_prev = first_prev
        first_prev = item

In [16]:
class Trigrams(IterableDataset):
    def __init__(self, text_file, vocabulary_size):
        self.vocab = build_vocab_from_iterator(
            file_words(text_file),
            max_tokens = vocabulary_size,
            specials = ['<unk>']
        )
        self.vocab.set_default_index(self.vocab['<unk>'])
        self.vocabulary_size = vocabulary_size
        self.text_file = text_file

    def __iter__(self):
        return iterator_look((self.vocab[t] for t in chain.from_iterable(file_words(self.text_file))))

In [17]:
def training(xx):
  train_dataset_new = Trigrams('train_new.txt', vocab_size)
  model = SimpleTrigramNeuralLanguageModel(vocab_size, embed_size, hidden_size).to(device)
  optimizer = torch.optim.Adam(model.parameters())
  criterion = torch.nn.NLLLoss()
  data = DataLoader(train_dataset_new, batch_size=800)
  step = 0
  for epoch in range(1):
      model.train()
      for x, y in data:
          x = x.to(device)
          y = y.to(device)
          optimizer.zero_grad()
          outputs = model(x)
          loss = criterion(torch.log(outputs), y)
          if step % 100 == 0:
              print(step, loss)
          step += 1
          loss.backward()
          optimizer.step()
  torch.save(model.state_dict(), 'model2.bin')

In [ ]:
training(xx=0.0001)

0 tensor(11.2670, device='cuda:0', grad_fn=<NllLossBackward0>)
100 tensor(8.0867, device='cuda:0', grad_fn=<NllLossBackward0>)
200 tensor(6.8976, device='cuda:0', grad_fn=<NllLossBackward0>)
300 tensor(6.6515, device='cuda:0', grad_fn=<NllLossBackward0>)
400 tensor(6.6224, device='cuda:0', grad_fn=<NllLossBackward0>)
500 tensor(6.7443, device='cuda:0', grad_fn=<NllLossBackward0>)
600 tensor(6.7064, device='cuda:0', grad_fn=<NllLossBackward0>)
700 tensor(6.8224, device='cuda:0', grad_fn=<NllLossBackward0>)
800 tensor(6.8516, device='cuda:0', grad_fn=<NllLossBackward0>)
900 tensor(6.6103, device='cuda:0', grad_fn=<NllLossBackward0>)
1000 tensor(6.5455, device='cuda:0', grad_fn=<NllLossBackward0>)
1100 tensor(6.8369, device='cuda:0', grad_fn=<NllLossBackward0>)
1200 tensor(6.5587, device='cuda:0', grad_fn=<NllLossBackward0>)
1300 tensor(6.2804, device='cuda:0', grad_fn=<NllLossBackward0>)
1400 tensor(6.5476, device='cuda:0', grad_fn=<NllLossBackward0>)
1500 tensor(6.7563, device='cuda:0',

In [ ]:
model = SimpleTrigramNeuralLanguageModel(vocab_size, embed_size, hidden_size).to(device)
model.load_state_dict(torch.load('model2.bin'))
model.eval()
train_dataset_new = Trigrams('train_new.txt', vocab_size)

def predict_words(words):
    ixs = torch.tensor(train_dataset_new.vocab.forward(['with'])).to(device)
    predictions = model(ixs)
    total_prob = 0.0
    prediction = ''
    top = torch.topk(predictions[0], 30)
    top_indices = top.indices.tolist()
    top_probs = top.values.tolist()
    top_words = train_dataset_new.vocab.lookup_tokens(top_indices)
    top_preds = list(zip(top_words, top_indices, top_probs))

    for word, _, prob in top_preds:
        if word != '<unk>':
            prediction += f'{word}:{prob} '
            total_prob += prob
    prediction += f':{1 - total_prob}'
    return prediction

In [ ]:
model = SimpleTrigramNeuralLanguageModel(vocab_size, embed_size, hidden_size).to(device)
model.load_state_dict(torch.load('model2.bin'))
model.eval() 

In [ ]:
with lzma.open(f'dev-0/in.tsv.xz', mode='rt', encoding='utf-8') as fid:
      with open(f'dev-0/out-HIDDEN-SIZE={hidden_size}.tsv', 'w', encoding='utf-8', newline='\n') as f:
          for line in fid:
              separated = line.split('\t')
              prefix = separated[6].replace(r'\n', ' ').split()[-2:]
              output_line = predict_words(prefix)
              f.write(output_line + '\n')

In [ ]:
with lzma.open(f'test-A/in.tsv.xz', mode='rt', encoding='utf-8') as fid:
      with open(f'test-A/out-HIDDEN-SIZE={hidden_size}.tsv', 'w', encoding='utf-8', newline='\n') as f:
          for line in fid:
              separated = line.split('\t')
              prefix = separated[6].replace(r'\n', ' ').split()[-2:]
              output_line = predict_words(prefix)
              f.write(output_line + '\n')

In [ ]:
torch.save(model.state_dict(), 'model2.bin')